In [1]:
# !pip install langchain openai chromadb tiktoken pypdf panel

In [2]:
# pip install --upgrade langchain

In [1]:
## import libraries
import os 
from langchain.llms import OpenAI
from langchain.chains import RetrievalQA
from langchain.document_loaders import TextLoader
from langchain.document_loaders import PyPDFLoader
from langchain.indexes import VectorstoreIndexCreator
from langchain.text_splitter import CharacterTextSplitter
from langchain.embeddings import OpenAIEmbeddings
from langchain.vectorstores import Chroma
import panel as pn
import tempfile

In [2]:
## panel extension
pn.extension('texteditor', template="bootstrap", sizing_mode='stretch_width')
pn.state.template.param.update(
    main_max_width="690px",
    header_background="#F08080",
)

In [9]:
## create widgets
file_input = pn.widgets.FileInput(width=300)

openaikey = pn.widgets.PasswordInput(value="", placeholder="Enter your OpenAI API Key here...", width=300)
prompt = pn.widgets.TextEditor(
    value="", placeholder="Enter your questions here...", height=160, toolbar=False
)
run_button = pn.widgets.Button(name="Run!")


select_k = pn.widgets.IntSlider(
    name="Number of relevant chunks", start=1, end=5, step=1, value=1
)
select_temperature = pn.widgets.FloatInput(
    name="Temperature", start=0, end=1, step=0.01, value=0
)
select_chain_type = pn.widgets.RadioButtonGroup(
    name='Chain type', 
    options=['stuff', 'map_reduce', "refine", "map_rerank"]
)

widgets = pn.Row(
    pn.Column(prompt, run_button, margin=5),
    pn.Card(
        "Chain type:",
        pn.Column(select_chain_type, select_k,select_temperature),
        title="Advanced settings", margin=10
    ), width=600
)

In [10]:
file_input

FileInput(width=300)

In [11]:
file_input.value

In [12]:
openaikey

PasswordInput(placeholder='Enter your OpenAI A..., width=300)

In [13]:
openaikey.value

''

In [14]:
widgets

Row(width=600)
    [0] Column(margin=5, sizing_mode='stretch_width')
        [0] TextEditor(height=160, placeholder='Enter your questions h..., sizing_mode='stretch_width', toolbar=False)
        [1] Button(name='Run!', sizing_mode='stretch_width')
    [1] Card(margin=10, sizing_mode='stretch_width', title='Advanced settings')
        [0] Markdown(str, sizing_mode='stretch_width')
        [1] Column(sizing_mode='stretch_width')
            [0] RadioButtonGroup(name='Chain type', options=['stuff', 'map_reduce', ...], sizing_mode='stretch_width', value='stuff')
            [1] IntSlider(end=5, name='Number of relevant c..., sizing_mode='stretch_width', start=1, value=1)
            [2] FloatInput(end=1, name='Temperature', sizing_mode='stretch_width', start=0, step=0.01)

In [15]:
select_temperature.value

0

In [24]:
def qa(file, query, chain_type, k,temperature_value):
    # load document
    loader = PyPDFLoader(file)
    documents = loader.load()
    # split the documents into chunks
    text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=0)
    texts = text_splitter.split_documents(documents)
    # select which embeddings we want to use
    embeddings = OpenAIEmbeddings()
#     embeddings = OpenAIEmbeddings(model='text-search-ada-doc-001')
    # create the vectorestore to use as the index
    db = Chroma.from_documents(texts, embeddings)
    # expose this index in a retriever interface
    retriever = db.as_retriever(search_type="similarity", search_kwargs={"k": k})
    # create a chain to answer questions
    qa_chain = RetrievalQA.from_chain_type(
    llm=OpenAI(temperature=temperature_value), chain_type=chain_type, retriever=retriever, return_source_documents=True)
    result = qa_chain({"query": query})
    print(result['result'])
    return result

In [18]:
# os.environ["OPENAI_API_KEY"] = ''

In [14]:
# pip install pypdf

In [15]:
# pip install openai

In [16]:
# pip install --upgrade setuptools

In [17]:
# pip install chromadb

In [18]:
# pip install hnswlib

In [19]:
# pip install tiktoken

In [6]:
# result = qa("ai_index.pdf", "what is the summary of the document",'stuff',2,0.5)

In [7]:
# result

In [17]:
convos = []  # store all panel objects in a list

def qa_result(_):
    os.environ["OPENAI_API_KEY"] = openaikey.value
    
    # save pdf file to a temp file 
    if file_input.value is not None:
        file_input.save("temp.pdf")
    
        prompt_text = prompt.value
        print(prompt_text)
        if prompt_text:
            result = qa(file="temp.pdf", query=prompt_text, chain_type=select_chain_type.value, k=select_k.value,temperature_value=select_temperature.value)
            print(result)
            convos.extend([
                pn.Row(
                    pn.panel("\U0001F60A", width=10),
                    prompt_text,
                    width=600
                ),
                pn.Row(
                    pn.panel("\U0001F916", width=10),
                    pn.Column(
                        result["result"],
#                         "Relevant source text:",
#                         pn.pane.Markdown('\n--------------------------------------------------------------------\n'.join(doc.page_content for doc in result["source_documents"]))
                    )
                )
            ])
            #return convos
    return pn.Column(*convos, margin=15, width=575, min_height=300)

In [19]:
# prompt

TextEditor(height=160, placeholder='Enter your questions h..., sizing_mode='stretch_width', toolbar=False)

In [20]:
# prompt.value

'<p>How many AI publications in 2021</p>'

In [23]:
# select_chain_type.value, select_k.value,select_temperature.value

('stuff', 2, 0.6)

In [21]:
# pn.Row(
#                     pn.panel("\U0001F60A", width=10),
#                     prompt.value,
#                     width=600)

Row(width=600)
    [0] Markdown(str, width=10)
    [1] Markdown(str, sizing_mode='stretch_width')

In [22]:
#   pn.Row(
#                     pn.panel("\U0001F916", width=10),
#                     pn.Column(
#                         result["result"],
#                         "Relevant source text:",
#                         pn.pane.Markdown('\n--------------------------------------------------------------------\n'.join(doc.page_content for doc in result["source_documents"]))
#                     )
#                 )

Row(sizing_mode='stretch_width')
    [0] Markdown(str, width=10)
    [1] Column(sizing_mode='stretch_width')
        [0] Markdown(str, sizing_mode='stretch_width')
        [1] Markdown(str, sizing_mode='stretch_width')
        [2] Markdown(str, sizing_mode='stretch_width')

In [18]:
qa_interactive = pn.panel(
    pn.bind(qa_result, run_button),
    loading_indicator=True,
)

In [ ]:
# qa_result(_)

In [19]:
output = pn.WidgetBox('*Output will display here:*', qa_interactive, width=600,height=350, scroll=True)

In [22]:
# output

In [20]:
# Create a button to clear the chat output
clear_button = pn.widgets.Button(name='Clear')

In [21]:
# Define the callback function for the clear button
def clear_output(_):
    global convos
    convos=[]  # Clear the chat output

In [22]:
# Set the callback function for the clear button
clear_button.on_click(clear_output)

Watcher(inst=Button(name='Clear', sizing_mode='stretch_width'), cls=<class 'panel.widgets.button.Button'>, fn=<function clear_output at 0x00000227E5BC76D0>, mode='args', onlychanged=False, parameter_names=('clicks',), what='value', queued=False, precedence=0)

In [32]:
# output.append(qa_interactive)

In [33]:
# pn.bind(clr,clr_button)

In [34]:
# output

In [30]:
# clr_button = pn.widgets.Button(name="Clear",width=280)

In [36]:
# clr=output.clear()  

In [37]:
# clr_button.on_click(output.clear())

In [38]:
# if clr_button.clicks>=1
# value=1
# output

In [39]:
# clear_button=pn.panel(pn.bind(clr,clr_button))
# clear=pn.WidgetBox(clear_button,clr_button)

In [23]:
# layout
pn.Column(
    pn.pane.Markdown("""
    ## \U0001F60A! Question Answering with your PDF file
    
    1) Upload a PDF   2) Enter OpenAI API key  3) Type a question and click "Run".
    
    """),
    pn.Row(file_input,openaikey),
    output,
    widgets,clear_button

).servable()

Traceback (most recent call last):
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\pyviz_comms\__init__.py", line 325, in _handle_msg
 self._on_msg(msg)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\panel\viewable.py", line 297, in _on_msg
 patch.apply_to_document(doc, comm.id if comm else None)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\protocol\messages\patch_doc.py", line 115, in apply_to_document
 invoke_with_curdoc(doc, lambda: doc.apply_json_patch(self.content, setter))
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\document\callbacks.py", line 408, in invoke_with_curdoc
 return f()
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\protocol\messages\patch_doc.py", line 115, in <lambda>
 invoke_with_curdoc(doc, lambda: doc.apply_json_patch(self.content, setter))
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\document\document.py", line 391, in apply_json_patch
 DocumentPatchedEvent.handle_json(self, event_json, references, setter)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\document\events.py", line 259, in handle_json
 handler(doc, event_json, references, setter)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\document\events.py", line 300, in _handle_json
 cb(event_json["msg_data"])
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\document\callbacks.py", line 355, in trigger_json_event
 model._trigger_event(event)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\util\callback_manager.py", line 119, in _trigger_event
 self.document.callbacks.notify_event(cast(Model, self), event, invoke)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\document\callbacks.py", line 247, in notify_event
 invoke_with_curdoc(doc, callback_invoker)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\document\callbacks.py", line 408, in invoke_with_curdoc
 return f()
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\bokeh\util\callback_manager.py", line 115, in invoke
 cast(EventCallbackWithEvent, callback)(event)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\panel\reactive.py", line 413, in _comm_event
 state._handle_exception(e)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\panel\io\state.py", line 408, in _handle_exception
 raise exception
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\panel\reactive.py", line 411, in _comm_event
 self._process_bokeh_event(doc, event)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\panel\reactive.py", line 348, in _process_bokeh_event
 self._process_event(event)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\panel\widgets\button.py", line 183, in _process_event
 self.param.trigger('value')
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\param\parameterized.py", line 1993, in trigger
 self_.set_param(**dict(params, **triggers))
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\param\parameterized.py", line 1929, in set_param
 return self_.update(kwargs)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\param\parameterized.py", line 1902, in update
 self_._batch_call_watchers()
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\param\parameterized.py", line 2063, in _batch_call_watchers
 self_._execute_watcher(watcher, events)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\param\parameterized.py", line 2025, in _execute_watcher
 watcher.fn(*args, **kwargs)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\panel\param.py", line 838, in _replace_pane
 new_object = self.eval(self.object)
 File "C:\Users\RuKo601\AppData\Local\anaconda3\lib\site-packages\panel\param.py", line 818, in eval
 return function(*args, **kwargs)
 File "C:

Column(sizing_mode='stretch_width')
    [0] Markdown(str, sizing_mode='stretch_width')
    [1] Row(sizing_mode='stretch_width')
        [0] FileInput(width=300)
        [1] PasswordInput(placeholder='Enter your OpenAI A..., width=300)
    [2] WidgetBox(height=350, scroll=True, sizing_mode='fixed', width=600)
        [0] Markdown(str, sizing_mode='stretch_width')
        [1] ParamFunction(function, _pane=Column, loading_indicator=True, sizing_mode='stretch_width')
    [3] Row(width=600)
        [0] Column(margin=5, sizing_mode='stretch_width')
            [0] TextEditor(height=160, placeholder='Enter your questions h..., sizing_mode='stretch_width', toolbar=False)
            [1] Button(name='Run!', sizing_mode='stretch_width')
        [1] Card(margin=10, sizing_mode='stretch_width', title='Advanced settings')
            [0] Markdown(str, sizing_mode='stretch_width')
            [1] Column(sizing_mode='stretch_width')
                [0] RadioButtonGroup(name='Chain type', options=['stuff', 'map_reduce', ...], sizing_mode='stretch_width', value='stuff')
                [1] IntSlider(end=5, name='Number of relevant c..., sizing_mode='stretch_width', start=1, value=1)
                [2] FloatInput(end=1, name='Temperature', sizing_mode='stretch_width', start=0, step=0.01)
    [4] Button(name='Clear', sizing_mode='stretch_width')

In [42]:
# print(clr_button.clicks)

In [8]:
# openaikey.value